# Kernelized Stein Gradient

This notebook accompanies the original blog post [here](https://www.sanyamkapoor.com/machine-learning/stein-gradient).

## Install Dependencies

We use [PyTorch](https://pytorch.org/) for all our differentiation needs and [Altair](https://altair-viz.github.io/) for plotting.

In [0]:
# Uncomment this if the imports throw an error
# ! pip install altair>=2.4 numpy>=1.16 torch>=1.0

In [0]:
import math
import numpy as np
import pandas as pd
import torch
import torch.autograd as autograd
import torch.optim as optim
import altair as alt

alt.data_transformers.enable('default', max_rows=None)

device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

### Drawing Utilities

In [0]:
def get_density_chart(P, d=7.0, step=0.1):
  xv, yv = torch.meshgrid([
      torch.arange(-d, d, step), 
      torch.arange(-d, d, step)
  ])
  pos_xy = torch.cat((xv.unsqueeze(-1), yv.unsqueeze(-1)), dim=-1)
  p_xy = P.log_prob(pos_xy.to(device)).exp().unsqueeze(-1).cpu()
  
  df = torch.cat([pos_xy, p_xy], dim=-1).numpy()
  df = pd.DataFrame({
      'x': df[:, :, 0].ravel(),
      'y': df[:, :, 1].ravel(),
      'p': df[:, :, 2].ravel(),
  })
  
  chart = alt.Chart(df).mark_point().encode(
    x='x:Q',
    y='y:Q',
    color=alt.Color('p:Q', scale=alt.Scale(scheme='viridis')),
    tooltip=['x','y','p']
  )
  
  return chart


def get_particles_chart(X):
  df = pd.DataFrame({
      'x': X[:, 0],
      'y': X[:, 1],
  })

  chart = alt.Chart(df).mark_circle(color='red').encode(
    x='x:Q',
    y='y:Q'
  )
  
  return chart

## RBF Kernel

In these experiments, we will use the *rbf* kernel. The kernel is defined as the squared exponential distance between the two vectors, parametrized by a bandwidth argument $\sigma$.

$$
k_{rbf}(\mathbf{x}, \mathbf{x}^\prime) = \exp{-\frac{1}{2\sigma^2}||\mathbf{x}-\mathbf{x}^\prime||^2}
$$

A vectorized version of the  kernel is given below. A few notes on the implementation follow.

In [0]:
class RBF(torch.nn.Module):
  def __init__(self, sigma=None):
    super(RBF, self).__init__()

    self.sigma = sigma

  def forward(self, X, Y):
    XX = X.matmul(X.t())
    XY = X.matmul(Y.t())
    YY = Y.matmul(Y.t())

    dnorm2 = -2 * XY + XX.diag().unsqueeze(1) + YY.diag().unsqueeze(0)

    # Apply the median heuristic (PyTorch does not give true median)
    if self.sigma is None:
      np_dnorm2 = dnorm2.detach().cpu().numpy()
      h = np.median(np_dnorm2) / (2 * np.log(X.size(0) + 1))
      sigma = np.sqrt(h).item()
    else:
      sigma = self.sigma

    gamma = 1.0 / (1e-8 + 2 * sigma ** 2)
    K_XY = (-gamma * dnorm2).exp()

    return K_XY
  
# Let us initialize a reusable instance right away.
K = RBF()

Selecting the bandwidth parameter $\sigma$ may be a painful task in itself. A popular heuristic chosen in literature is the *median* heuristic where we choose the bandwidth to be

$$
\sigma^2 = \frac{median^2}{2 \log{(n + 1)}}
$$

the median among distance of all pairs. This allows for gradient contribution from all the pairs when computing the gradient of the kernel during simulation of the ODE. Note that we use the `numpy` median function because the PyTorch median function does not behave as expected when the number of elements are even (and does not return the mean of the two central elements).

## Stein Variational Gradient Descent

We now simulate the following ODE for each particle $x_j$ in the system.

$$
\dot{x}_j = \frac{1}{n} \sum_{j = 1}^n \left[ k(x_j, x) \nabla_{x_j} \log{p(x_j)} + \nabla_{x_j} k(x_j, x)  \right]
$$

For stability reasons, we use Adam to allow for adaptive step size during the simulation. In fact, this can be replaced by any of the adaptive gradient descent techniques.

This is encapsulated in the `step` function below.

In [0]:
class SVGD:
  def __init__(self, P, K, optimizer):
    self.P = P
    self.K = K
    self.optim = optimizer

  def phi(self, X):
    X = X.detach().requires_grad_(True)

    log_prob = self.P.log_prob(X)
    score_func = autograd.grad(log_prob.sum(), X)[0]

    K_XX = self.K(X, X.detach())
    grad_K = -autograd.grad(K_XX.sum(), X)[0]

    phi = (K_XX.detach().matmul(score_func) + grad_K) / X.size(0)

    return phi

  def step(self, X):
    self.optim.zero_grad()
    X.grad = -self.phi(X)
    self.optim.step()

# Experiments

## Unimodal Gaussian

We will first run this on a Unimodal Gaussian. We initialize the particles in an overdispersed manner and see how they converge around the typical set of the distribution.

**NOTE**: Try increasing the number of particles $n$ and different initializations to see how the particles distribute themselves.

In [0]:
gauss = torch.distributions.MultivariateNormal(torch.Tensor([-0.6871,0.8010]).to(device),
        covariance_matrix=5 * torch.Tensor([[0.2260,0.1652],[0.1652,0.6779]]).to(device))

n = 10
X_init = (3 * torch.randn(n, *gauss.event_shape)).to(device)

In [0]:
gauss_chart = get_density_chart(gauss, d=7.0, step=0.1)

Let us see how this overdispersed initialization looks like. Note that initializations much farther away from the typical set of the distributions may take longer to converge.

In [8]:
gauss_chart + get_particles_chart(X_init.cpu().numpy())

LayerChart({
  layer: [Chart({
    data:                   p    x    y
    0      3.184421e-10 -7.0 -7.0
    1      3.563921e-10 -7.0 -6.9
    2      3.974355e-10 -7.0 -6.8
    3      4.416175e-10 -7.0 -6.7
    4      4.889510e-10 -7.0 -6.6
    5      5.394200e-10 -7.0 -6.5
    6      5.929660e-10 -7.0 -6.4
    7      6.494892e-10 -7.0 -6.3
    8      7.088541e-10 -7.0 -6.2
    9      7.708729e-10 -7.0 -6.1
    10     8.353108e-10 -7.0 -6.0
    11     9.018952e-10 -7.0 -5.9
    12     9.702943e-10 -7.0 -5.8
    13     1.040144e-09 -7.0 -5.7
    14     1.111023e-09 -7.0 -5.6
    15     1.182479e-09 -7.0 -5.5
    16     1.254026e-09 -7.0 -5.4
    17     1.325132e-09 -7.0 -5.3
    18     1.395253e-09 -7.0 -5.2
    19     1.463825e-09 -7.0 -5.1
    20     1.530259e-09 -7.0 -5.0
    21     1.593976e-09 -7.0 -4.9
    22     1.654396e-09 -7.0 -4.8
    23     1.710954e-09 -7.0 -4.7
    24     1.763112e-09 -7.0 -4.6
    25     1.810343e-09 -7.0 -4.5
    26     1.852179e-09 -7.0 -4.4
    27     1.888191e-09 -7.0 -4.3
    28     1.918006e-09 -7.0 -4.2
    29     1.941311e-09 -7.0 -4.1
    ...             ...  ...  ...
    19570  2.894681e-13  6.9  4.0
    19571  3.143477e-13  6.9  4.1
    19572  3.401425e-13  6.9  4.2
    19573  3.667352e-13  6.9  4.3
    19574  3.939902e-13  6.9  4.4
    19575  4.217540e-13  6.9  4.5
    19576  4.498565e-13  6.9  4.6
    19577  4.781122e-13  6.9  4.7
    19578  5.063220e-13  6.9  4.8
    19579  5.342749e-13  6.9  4.9
    19580  5.617508e-13  6.9  5.0
    19581  5.885235e-13  6.9  5.1
    19582  6.143605e-13  6.9  5.2
    19583  6.390361e-13  6.9  5.3
    19584  6.623211e-13  6.9  5.4
    19585  6.839947e-13  6.9  5.5
    19586  7.038440e-13  6.9  5.6
    19587  7.216767e-13  6.9  5.7
    19588  7.373099e-13  6.9  5.8
    19589  7.505796e-13  6.9  5.9
    19590  7.613533e-13  6.9  6.0
    19591  7.695114e-13  6.9  6.1
    19592  7.749730e-13  6.9  6.2
    19593  7.776738e-13  6.9  6.3
    19594  7.775908e-13  6.9  6.4
    19595  7.747188e-13  6.9  6.5
    19596  7.690946e-13  6.9  6.6
    19597  7.607726e-13  6.9  6.7
    19598  7.498442e-13  6.9  6.8
    19599  7.364272e-13  6.9  6.9
    
    [19600 rows x 3 columns],
    encoding: EncodingWithFacet({
      color: Color({
        scale: Scale({
          scheme: 'viridis'
        }),
        shorthand: 'p:Q'
      }),
      tooltip: [Tooltip({
        shorthand: 'x'
      }), Tooltip({
        shorthand: 'y'
      }), Tooltip({
        shorthand: 'p'
      })],
      x: X({
        shorthand: 'x:Q'
      }),
      y: Y({
        shorthand: 'y:Q'
      })
    }),
    mark: 'point'
  }), Chart({
    data:           x         y
    0 -0.275793 -1.632378
    1 -1.117821 -3.123454
    2  5.052466 -6.183845
    3 -4.719897  4.449635
    4  1.668821  0.219508
    5 -0.210910 -2.530870
    6  3.553493  1.186212
    7  0.072033 -0.541355
    8  0.608334 -3.216434
    9  3.044670  3.625674,
    encoding: EncodingWithFacet({
      x: X({
        shorthand: 'x:Q'
      }),
      y: Y({
        shorthand: 'y:Q'
      })
    }),
    mark: MarkDef({
      color: 'red',
      type: 'circle'
    })
  })]
})

In [0]:
X = X_init.clone()
svgd = SVGD(gauss, K, optim.Adam([X], lr=1e-1))
for _ in range(1000):
    svgd.step(X)

In [10]:
gauss_chart + get_particles_chart(X.cpu().numpy())

LayerChart({
  layer: [Chart({
    data:                   p    x    y
    0      3.184421e-10 -7.0 -7.0
    1      3.563921e-10 -7.0 -6.9
    2      3.974355e-10 -7.0 -6.8
    3      4.416175e-10 -7.0 -6.7
    4      4.889510e-10 -7.0 -6.6
    5      5.394200e-10 -7.0 -6.5
    6      5.929660e-10 -7.0 -6.4
    7      6.494892e-10 -7.0 -6.3
    8      7.088541e-10 -7.0 -6.2
    9      7.708729e-10 -7.0 -6.1
    10     8.353108e-10 -7.0 -6.0
    11     9.018952e-10 -7.0 -5.9
    12     9.702943e-10 -7.0 -5.8
    13     1.040144e-09 -7.0 -5.7
    14     1.111023e-09 -7.0 -5.6
    15     1.182479e-09 -7.0 -5.5
    16     1.254026e-09 -7.0 -5.4
    17     1.325132e-09 -7.0 -5.3
    18     1.395253e-09 -7.0 -5.2
    19     1.463825e-09 -7.0 -5.1
    20     1.530259e-09 -7.0 -5.0
    21     1.593976e-09 -7.0 -4.9
    22     1.654396e-09 -7.0 -4.8
    23     1.710954e-09 -7.0 -4.7
    24     1.763112e-09 -7.0 -4.6
    25     1.810343e-09 -7.0 -4.5
    26     1.852179e-09 -7.0 -4.4
    27     1.888191e-09 -7.0 -4.3
    28     1.918006e-09 -7.0 -4.2
    29     1.941311e-09 -7.0 -4.1
    ...             ...  ...  ...
    19570  2.894681e-13  6.9  4.0
    19571  3.143477e-13  6.9  4.1
    19572  3.401425e-13  6.9  4.2
    19573  3.667352e-13  6.9  4.3
    19574  3.939902e-13  6.9  4.4
    19575  4.217540e-13  6.9  4.5
    19576  4.498565e-13  6.9  4.6
    19577  4.781122e-13  6.9  4.7
    19578  5.063220e-13  6.9  4.8
    19579  5.342749e-13  6.9  4.9
    19580  5.617508e-13  6.9  5.0
    19581  5.885235e-13  6.9  5.1
    19582  6.143605e-13  6.9  5.2
    19583  6.390361e-13  6.9  5.3
    19584  6.623211e-13  6.9  5.4
    19585  6.839947e-13  6.9  5.5
    19586  7.038440e-13  6.9  5.6
    19587  7.216767e-13  6.9  5.7
    19588  7.373099e-13  6.9  5.8
    19589  7.505796e-13  6.9  5.9
    19590  7.613533e-13  6.9  6.0
    19591  7.695114e-13  6.9  6.1
    19592  7.749730e-13  6.9  6.2
    19593  7.776738e-13  6.9  6.3
    19594  7.775908e-13  6.9  6.4
    19595  7.747188e-13  6.9  6.5
    19596  7.690946e-13  6.9  6.6
    19597  7.607726e-13  6.9  6.7
    19598  7.498442e-13  6.9  6.8
    19599  7.364272e-13  6.9  6.9
    
    [19600 rows x 3 columns],
    encoding: EncodingWithFacet({
      color: Color({
        scale: Scale({
          scheme: 'viridis'
        }),
        shorthand: 'p:Q'
      }),
      tooltip: [Tooltip({
        shorthand: 'x'
      }), Tooltip({
        shorthand: 'y'
      }), Tooltip({
        shorthand: 'p'
      })],
      x: X({
        shorthand: 'x:Q'
      }),
      y: Y({
        shorthand: 'y:Q'
      })
    }),
    mark: 'point'
  }), Chart({
    data:           x         y
    0 -0.489534  1.405959
    1 -1.546800 -1.831452
    2 -0.315349 -0.886390
    3 -1.628732  1.108514
    4 -1.058851  2.488389
    5 -1.983109 -0.341739
    6  0.254533  0.493485
    7  0.608909  1.943739
    8 -0.884666  0.196042
    9  0.172600  3.433452,
    encoding: EncodingWithFacet({
      x: X({
        shorthand: 'x:Q'
      }),
      y: Y({
        shorthand: 'y:Q'
      })
    }),
    mark: MarkDef({
      color: 'red',
      type: 'circle'
    })
  })]
})

## Mixture of Gaussians

The exact same simulation without any manual fine tuning works even for a multimodal Gaussian. We will first create a generic PyTorch distribution which can help us build multiple kinds of Mixture of Gaussians.

In [0]:
class MoG(torch.distributions.Distribution):
  def __init__(self, loc, covariance_matrix):
    self.num_components = loc.size(0)
    self.loc = loc
    self.covariance_matrix = covariance_matrix

    self.dists = [
      torch.distributions.MultivariateNormal(mu, covariance_matrix=sigma)
      for mu, sigma in zip(loc, covariance_matrix)
    ]
    
    super(MoG, self).__init__(torch.Size([]), torch.Size([loc.size(-1)]))

  @property
  def arg_constraints(self):
    return self.dists[0].arg_constraints

  @property
  def support(self):
    return self.dists[0].support

  @property
  def has_rsample(self):
    return False

  def log_prob(self, value):
    return torch.cat(
      [p.log_prob(value).unsqueeze(-1) for p in self.dists], dim=-1).logsumexp(dim=-1)

  def enumerate_support(self):
    return self.dists[0].enumerate_support()

### Mixture of Two Gaussians

Here we create a mixture of two Gaussians where the means are symmetrically placed at $x=|5|$ and the covariance matrix is given by $\begin{pmatrix}0.5 & 0 \\ 0 & 0.5\end{pmatrix}$.

In [0]:
class MoG2(MoG):
  def __init__(self, device=None):
    loc = torch.Tensor([[-5.0, 0.0], [5.0, 0.0]]).to(device)
    cov = torch.Tensor([0.5, 0.5]).diag().unsqueeze(0).repeat(2, 1, 1).to(device)

    super(MoG2, self).__init__(loc, cov)
    
mog2 = MoG2(device=device)

In [0]:
n = 100
X_init = (5 * torch.randn(n, *mog2.event_shape)).to(device)

In [0]:
X = X_init.clone()
svgd = SVGD(mog2, K, optim.Adam([X], lr=1e-1))
for _ in range(1000):
    svgd.step(X)

In [15]:
mog2_chart = get_density_chart(mog2, d=7.0, step=0.1)

(mog2_chart + get_particles_chart(X_init.cpu().numpy())) | (mog2_chart + get_particles_chart(X.cpu().numpy()))

HConcatChart({
  hconcat: [LayerChart({
    layer: [Chart({
      data:                   p    x    y
      0      3.056629e-24 -7.0 -7.0
      1      1.227190e-23 -7.0 -6.9
      2      4.829418e-23 -7.0 -6.8
      3      1.862909e-22 -7.0 -6.7
      4      7.043752e-22 -7.0 -6.6
      5      2.610531e-21 -7.0 -6.5
      6      9.483509e-21 -7.0 -6.4
      7      3.376939e-20 -7.0 -6.3
      8      1.178677e-19 -7.0 -6.2
      9      4.032522e-19 -7.0 -6.1
      10     1.352288e-18 -7.0 -6.0
      11     4.445075e-18 -7.0 -5.9
      12     1.432197e-17 -7.0 -5.8
      13     4.523197e-17 -7.0 -5.7
      14     1.400228e-16 -7.0 -5.6
      15     4.248780e-16 -7.0 -5.5
      16     1.263704e-15 -7.0 -5.4
      17     3.684175e-15 -7.0 -5.3
      18     1.052808e-14 -7.0 -5.2
      19     2.948986e-14 -7.0 -5.1
      20     8.096741e-14 -7.0 -5.0
      21     2.179022e-13 -7.0 -4.9
      22     5.748125e-13 -7.0 -4.8
      23     1.486305e-12 -7.0 -4.7
      24     3.767040e-12 -7.0 -4.6
      25     9.358543e-12 -7.0 -4.5
      26     2.278929e-11 -7.0 -4.4
      27     5.439596e-11 -7.0 -4.3
      28     1.272676e-10 -7.0 -4.2
      29     2.918652e-10 -7.0 -4.1
      ...             ...  ...  ...
      19570  9.690255e-10  6.9  4.0
      19571  4.310790e-10  6.9  4.1
      19572  1.879717e-10  6.9  4.2
      19573  8.034173e-11  6.9  4.3
      19574  3.365933e-11  6.9  4.4
      19575  1.382238e-11  6.9  4.5
      19576  5.563843e-12  6.9  4.6
      19577  2.195243e-12  6.9  4.7
      19578  8.489865e-13  6.9  4.8
      19579  3.218372e-13  6.9  4.9
      19580  1.195872e-13  6.9  5.0
      19581  4.355593e-14  6.9  5.1
      19582  1.554979e-14  6.9  5.2
      19583  5.441432e-15  6.9  5.3
      19584  1.866458e-15  6.9  5.4
      19585  6.275363e-16  6.9  5.5
      19586  2.068101e-16  6.9  5.6
      19587  6.680671e-17  6.9  5.7
      19588  2.115327e-17  6.9  5.8
      19589  6.565287e-18  6.9  5.9
      19590  1.997303e-18  6.9  6.0
      19591  5.955953e-19  6.9  6.1
      19592  1.740882e-19  6.9  6.2
      19593  4.987671e-20  6.9  6.3
      19594  1.400695e-20  6.9  6.4
      19595  3.855701e-21  6.9  6.5
      19596  1.040348e-21  6.9  6.6
      19597  2.751479e-22  6.9  6.7
      19598  7.132953e-23  6.9  6.8
      19599  1.812535e-23  6.9  6.9
      
      [19600 rows x 3 columns],
      encoding: EncodingWithFacet({
        color: Color({
          scale: Scale({
            scheme: 'viridis'
          }),
          shorthand: 'p:Q'
        }),
        tooltip: [Tooltip({
          shorthand: 'x'
        }), Tooltip({
          shorthand: 'y'
        }), Tooltip({
          shorthand: 'p'
        })],
        x: X({
          shorthand: 'x:Q'
        }),
        y: Y({
          shorthand: 'y:Q'
        })
      }),
      mark: 'point'
    }), Chart({
      data:             x          y
      0   -3.601659   3.151134
      1  -11.458320  -4.304109
      2    5.352246 -12.877615
      3   -4.342840   8.271852
      4    4.205091  -3.385797
      5   -0.012663   1.851774
      6   11.666947  -3.722419
      7   -3.626791  -7.801480
      8    0.856528  -7.404488
      9    4.946277   6.428208
      10   2.378933   8.005761
      11   1.260115   3.993903
      12   3.858907  -0.902007
      13  -5.354064  -0.689151
      14   0.196346  -2.940182
      15  -5.356923  -5.233626
      16   1.962974  -6.729161
      17  -4.492460   0.912753
      18  -2.236835   4.917802
      19   3.690978  -0.778494
      20  -2.495695   0.533911
      21  -0.645365  -4.302784
      22  -9.484643  -0.359307
      23  -0.196449   2.805857
      24  -2.405331  -0.072494
      25   2.872652   1.395963
      26   2.926879  -3.262476
      27  -1.276108   5.213814
      28  -5.009836  -4.724877
      29   8.542493   5.245967
      ..        ...        ...
      70   0.659034  -2.627646
      71  -5.384604  -4.938792
      72  -2.284777 -10.825177
      73   2.896479  -4.544779
      74  -8.049424   4.102871
      75   4.610175   7.645557

### Mixture of Six Gaussians

Here we create a mixture of six Gaussians where the means are spread around a circle of radius $5$and the covariance matrix is given by $\begin{pmatrix}0.5 & 0 \\ 0 & 0.5\end{pmatrix}$.

In [0]:
class MoG6(MoG):
  def __init__(self, device=None):
    def _compute_mu(i):
      return 5.0 * torch.Tensor([[
        torch.tensor(i * math.pi / 3.0).sin(),
        torch.tensor(i * math.pi / 3.0).cos()]])

    loc = torch.cat([_compute_mu(i) for i in range(1, 7)], dim=0).to(device)
    cov = torch.Tensor([0.5, 0.5]).diag().unsqueeze(0).to(device).repeat(6, 1, 1)

    super(MoG6, self).__init__(loc, cov)

mog6 = MoG6(device=device)

In [0]:
n = 100
X_init = (5 * torch.randn(n, *mog6.event_shape)).to(device)

In [0]:
X = X_init.clone()
svgd = SVGD(mog6, K, optim.Adam([X], lr=1e-1))
for _ in range(1000):
    svgd.step(X)

In [19]:
mog6_chart = get_density_chart(mog6, d=7.0, step=0.1)

(mog6_chart + get_particles_chart(X_init.cpu().numpy())) | (mog6_chart + get_particles_chart(X.cpu().numpy()))

HConcatChart({
  hconcat: [LayerChart({
    layer: [Chart({
      data:                   p    x    y
      0      4.098624e-13 -7.0 -7.0
      1      9.980674e-13 -7.0 -6.9
      2      2.382291e-12 -7.0 -6.8
      3      5.573754e-12 -7.0 -6.7
      4      1.278234e-11 -7.0 -6.6
      5      2.873352e-11 -7.0 -6.5
      6      6.331138e-11 -7.0 -6.4
      7      1.367379e-10 -7.0 -6.3
      8      2.894746e-10 -7.0 -6.2
      9      6.006828e-10 -7.0 -6.1
      10     1.221785e-09 -7.0 -6.0
      11     2.435883e-09 -7.0 -5.9
      12     4.760295e-09 -7.0 -5.8
      13     9.118570e-09 -7.0 -5.7
      14     1.712111e-08 -7.0 -5.6
      15     3.151025e-08 -7.0 -5.5
      16     5.684402e-08 -7.0 -5.4
      17     1.005154e-07 -7.0 -5.3
      18     1.742191e-07 -7.0 -5.2
      19     2.959861e-07 -7.0 -5.1
      20     4.929032e-07 -7.0 -5.0
      21     8.045737e-07 -7.0 -4.9
      22     1.287312e-06 -7.0 -4.8
      23     2.018913e-06 -7.0 -4.7
      24     3.103584e-06 -7.0 -4.6
      25     4.676535e-06 -7.0 -4.5
      26     6.907148e-06 -7.0 -4.4
      27     9.999726e-06 -7.0 -4.3
      28     1.419029e-05 -7.0 -4.2
      29     1.973824e-05 -7.0 -4.1
      ...             ...  ...  ...
      19570  4.544628e-05  6.9  4.0
      19571  3.333242e-05  6.9  4.1
      19572  2.396349e-05  6.9  4.2
      19573  1.688675e-05  6.9  4.3
      19574  1.166427e-05  6.9  4.4
      19575  7.897372e-06  6.9  4.5
      19576  5.241098e-06  6.9  4.6
      19577  3.409381e-06  6.9  4.7
      19578  2.173916e-06  6.9  4.8
      19579  1.358702e-06  6.9  4.9
      19580  8.323761e-07  6.9  5.0
      19581  4.998390e-07  6.9  5.1
      19582  2.942078e-07  6.9  5.2
      19583  1.697428e-07  6.9  5.3
      19584  9.599389e-08  6.9  5.4
      19585  5.321213e-08  6.9  5.5
      19586  2.891284e-08  6.9  5.6
      19587  1.539875e-08  6.9  5.7
      19588  8.038826e-09  6.9  5.8
      19589  4.113536e-09  6.9  5.9
      19590  2.063254e-09  6.9  6.0
      19591  1.014390e-09  6.9  6.1
      19592  4.888429e-10  6.9  6.2
      19593  2.309121e-10  6.9  6.3
      19594  1.069157e-10  6.9  6.4
      19595  4.852327e-11  6.9  6.5
      19596  2.158581e-11  6.9  6.6
      19597  9.412533e-12  6.9  6.7
      19598  4.023048e-12  6.9  6.8
      19599  1.685458e-12  6.9  6.9
      
      [19600 rows x 3 columns],
      encoding: EncodingWithFacet({
        color: Color({
          scale: Scale({
            scheme: 'viridis'
          }),
          shorthand: 'p:Q'
        }),
        tooltip: [Tooltip({
          shorthand: 'x'
        }), Tooltip({
          shorthand: 'y'
        }), Tooltip({
          shorthand: 'p'
        })],
        x: X({
          shorthand: 'x:Q'
        }),
        y: Y({
          shorthand: 'y:Q'
        })
      }),
      mark: 'point'
    }), Chart({
      data:             x          y
      0   -4.040068  -6.010101
      1   -4.342675  -3.369222
      2    6.648109  -4.602563
      3    4.836421  -0.272676
      4   -3.561516   1.153899
      5    4.099842  -0.394213
      6   -0.549779   3.381063
      7    2.572057   3.753982
      8    1.062016 -10.564462
      9    9.283065   0.744016
      10  -6.775406   7.331171
      11  -6.111000  -5.320908
      12   0.048358   1.963068
      13   7.842107   2.226172
      14  -8.164411  -2.876634
      15  -2.247254  -2.554330
      16   0.364904  -1.989399
      17  -1.927123  -4.800048
      18  -3.983644  -1.341064
      19  -0.009444   9.594393
      20   3.371983  -2.238862
      21   4.348473   6.341508
      22   4.661050   3.853831
      23  -6.455284   0.793340
      24   8.159105   7.200937
      25   2.230751  -5.931673
      26  -1.320003  -5.892489
      27 -12.873230  -8.377059
      28  -3.451494  -0.866565
      29   7.133263   7.796342
      ..        ...        ...
      70 -10.297341  12.899423
      71   0.575043   7.523794
      72   3.221913   2.628790
      73   1.120273   1.197813
      74  -1.156276  -3.289879
      75   2.392795   3.747736

## Mixture of Six Gaussians with One Particle

As we've noted in the blog post, using the one particle and a kernel where $\nabla_xk(x,x) = 0$, we achieve the classic MAP estimator. *rbf* kernel satisfies the gradient property. Let us see whether we get a MAP estimator. We should expect, just like in the classic mode-finding setting that the particle should end up in different modes for different runs.

In [0]:
X_init = (5 * torch.randn(1, *mog6.event_shape)).to(device)
X = X_init.clone()
svgd = SVGD(mog6, K, optim.Adam([X], lr=1e-1))

for _ in range(1000):
    svgd.step(X)

In [21]:
(mog6_chart + get_particles_chart(X_init.cpu().numpy())) | (mog6_chart + get_particles_chart(X.cpu().numpy()))

HConcatChart({
  hconcat: [LayerChart({
    layer: [Chart({
      data:                   p    x    y
      0      4.098624e-13 -7.0 -7.0
      1      9.980674e-13 -7.0 -6.9
      2      2.382291e-12 -7.0 -6.8
      3      5.573754e-12 -7.0 -6.7
      4      1.278234e-11 -7.0 -6.6
      5      2.873352e-11 -7.0 -6.5
      6      6.331138e-11 -7.0 -6.4
      7      1.367379e-10 -7.0 -6.3
      8      2.894746e-10 -7.0 -6.2
      9      6.006828e-10 -7.0 -6.1
      10     1.221785e-09 -7.0 -6.0
      11     2.435883e-09 -7.0 -5.9
      12     4.760295e-09 -7.0 -5.8
      13     9.118570e-09 -7.0 -5.7
      14     1.712111e-08 -7.0 -5.6
      15     3.151025e-08 -7.0 -5.5
      16     5.684402e-08 -7.0 -5.4
      17     1.005154e-07 -7.0 -5.3
      18     1.742191e-07 -7.0 -5.2
      19     2.959861e-07 -7.0 -5.1
      20     4.929032e-07 -7.0 -5.0
      21     8.045737e-07 -7.0 -4.9
      22     1.287312e-06 -7.0 -4.8
      23     2.018913e-06 -7.0 -4.7
      24     3.103584e-06 -7.0 -4.6
      25     4.676535e-06 -7.0 -4.5
      26     6.907148e-06 -7.0 -4.4
      27     9.999726e-06 -7.0 -4.3
      28     1.419029e-05 -7.0 -4.2
      29     1.973824e-05 -7.0 -4.1
      ...             ...  ...  ...
      19570  4.544628e-05  6.9  4.0
      19571  3.333242e-05  6.9  4.1
      19572  2.396349e-05  6.9  4.2
      19573  1.688675e-05  6.9  4.3
      19574  1.166427e-05  6.9  4.4
      19575  7.897372e-06  6.9  4.5
      19576  5.241098e-06  6.9  4.6
      19577  3.409381e-06  6.9  4.7
      19578  2.173916e-06  6.9  4.8
      19579  1.358702e-06  6.9  4.9
      19580  8.323761e-07  6.9  5.0
      19581  4.998390e-07  6.9  5.1
      19582  2.942078e-07  6.9  5.2
      19583  1.697428e-07  6.9  5.3
      19584  9.599389e-08  6.9  5.4
      19585  5.321213e-08  6.9  5.5
      19586  2.891284e-08  6.9  5.6
      19587  1.539875e-08  6.9  5.7
      19588  8.038826e-09  6.9  5.8
      19589  4.113536e-09  6.9  5.9
      19590  2.063254e-09  6.9  6.0
      19591  1.014390e-09  6.9  6.1
      19592  4.888429e-10  6.9  6.2
      19593  2.309121e-10  6.9  6.3
      19594  1.069157e-10  6.9  6.4
      19595  4.852327e-11  6.9  6.5
      19596  2.158581e-11  6.9  6.6
      19597  9.412533e-12  6.9  6.7
      19598  4.023048e-12  6.9  6.8
      19599  1.685458e-12  6.9  6.9
      
      [19600 rows x 3 columns],
      encoding: EncodingWithFacet({
        color: Color({
          scale: Scale({
            scheme: 'viridis'
          }),
          shorthand: 'p:Q'
        }),
        tooltip: [Tooltip({
          shorthand: 'x'
        }), Tooltip({
          shorthand: 'y'
        }), Tooltip({
          shorthand: 'p'
        })],
        x: X({
          shorthand: 'x:Q'
        }),
        y: Y({
          shorthand: 'y:Q'
        })
      }),
      mark: 'point'
    }), Chart({
      data:           x         y
      0 -9.678164  5.938091,
      encoding: EncodingWithFacet({
        x: X({
          shorthand: 'x:Q'
        }),
        y: Y({
          shorthand: 'y:Q'
        })
      }),
      mark: MarkDef({
        color: 'red',
        type: 'circle'
      })
    })]
  }), LayerChart({
    layer: [Chart({
      data:                   p    x    y
      0      4.098624e-13 -7.0 -7.0
      1      9.980674e-13 -7.0 -6.9
      2      2.382291e-12 -7.0 -6.8
      3      5.573754e-12 -7.0 -6.7
      4      1.278234e-11 -7.0 -6.6
      5      2.873352e-11 -7.0 -6.5
      6      6.331138e-11 -7.0 -6.4
      7      1.367379e-10 -7.0 -6.3
      8      2.894746e-10 -7.0 -6.2
      9      6.006828e-10 -7.0 -6.1
      10     1.221785e-09 -7.0 -6.0
      11     2.435883e-09 -7.0 -5.9
      12     4.760295e-09 -7.0 -5.8
      13     9.118570e-09 -7.0 -5.7
      14     1.712111e-08 -7.0 -5.6
      15     3.151025e-08 -7.0 -5.5
      16     5.684402e-08 -7.0 -5.4
      17     1.005154e-07 -7.0 -5.3
      18     1.742191e-07 -7.0 -5.2
      19     2.959861e-07 -7.0 -5.1
      20     4.929032e-07 -7.0 -5.0
      21     8.045737e-07 -7.0 -4.9
      22  